In [3]:
import gensim

# Load the model
ft_model = gensim.models.FastText.load("ft_model1.model")




In [4]:
expression = 'vana + vakomana - vasikana'

positive = []
negative = []

parts = expression.replace('-', '+-').split('+')

for part in parts:
    part = part.strip()
    if part.startswith('-'):
        negative.append(part[1:].strip())
    elif part:
        positive.append(part)

print(positive)
print(negative)

['vana', 'vakomana']
['vasikana']


In [7]:

result_vector = ft_model.wv.get_vector(positive[0])  

# Add vectors for positive words
for word in positive[1:]:
    if word in ft_model.wv:
        result_vector += ft_model.wv.get_vector(word)
    else:
        raise KeyError(f"Word '{word}' not in vocabulary")

# Subtract vectors for negative words
for word in negative:
    if word in ft_model.wv:
        result_vector -= ft_model.wv.get_vector(word)
    else:
        raise KeyError(f"Word '{word}' not in vocabulary")

# Find similar words
result = ft_model.wv.most_similar(positive=[result_vector], topn=top_n)

# Format the results
response = [{'word': word, 'similarity': similarity} for word, similarity in result]


print(response)

ValueError: output array is read-only

In [9]:
import numpy as np

In [11]:
top_n = 5
if not positive:
    raise ValueError("Positive word list is empty.")
if not isinstance(positive, list) or not isinstance(negative, list):
    raise TypeError("Positive and negative should be lists.")

# Initialize result_vector with a writable copy of the first positive word vector
result_vector = ft_model.wv.get_vector(positive[0]).copy()  

# Add vectors for positive words
for word in positive[1:]:
    if word in ft_model.wv:
        result_vector += ft_model.wv.get_vector(word)
    else:
        raise KeyError(f"Word '{word}' not in vocabulary")

# Subtract vectors for negative words
for word in negative:
    if word in ft_model.wv:
        result_vector -= ft_model.wv.get_vector(word)
    else:
        raise KeyError(f"Word '{word}' not in vocabulary")

# Function to compute cosine similarity between vectors
def cosine_similarity(vec1, vec2):
    return np.dot(vec1, vec2) / (np.linalg.norm(vec1) * np.linalg.norm(vec2))

# Compute cosine similarities between result_vector and all words in the model's vocabulary
cosine_similarities = []
for word in ft_model.wv.index_to_key:
    word_vector = ft_model.wv.get_vector(word)
    similarity = cosine_similarity(result_vector, word_vector)
    cosine_similarities.append((word, similarity))

# Sort by similarity and return top_n results
sorted_similarities = sorted(cosine_similarities, key=lambda x: x[1], reverse=True)
top_results = sorted_similarities[:top_n]

# Format the results
response = [{'word': word, 'similarity': similarity} for word, similarity in top_results]
print(response)

[{'word': 'vana', 'similarity': 0.92390615}, {'word': 'nhevana', 'similarity': 0.7112871}, {'word': 'twevana', 'similarity': 0.6789861}, {'word': 'vanajib', 'similarity': 0.66515744}, {'word': 'svana', 'similarity': 0.6477824}]
